<a href="https://colab.research.google.com/github/0xstubbs/Rook-Governance/blob/main/Rook_Governance_Votes_by_Wallet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This notebook takes a look at Rook Token holders over time. The purpose is to: 

1.   Determine token distribution over time.
2.   Determine quorum requirements



In [6]:
import pandas as pd
import numpy as np
import altair as alt
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [7]:
!pip install altair_data_server

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


Open csv with token balance data downloaded from Dune Analytics.

In [8]:
df = pd.DataFrame()
csvs = [  '/content/gdrive/MyDrive/Colab Notebooks/2020_token_holder_balances.csv'
        , '/content/gdrive/MyDrive/Colab Notebooks/21-01-01---21-05-31_token_holder_balances.csv'
        , '/content/gdrive/MyDrive/Colab Notebooks/21-06-01_to_21-12-31_rook_token_holder_balances.csv'
        , '/content/gdrive/MyDrive/Colab Notebooks/22-0101_to_22-0725_token_holders.csv'
        ]
for csv in csvs:
  df_new = pd.read_csv(csv)
  df = pd.concat([df, df_new], ignore_index = True)
  # df.append(df_new)

df['day'] = pd.to_datetime(df['day'])
df['rook_token_balance']=df['rook_token_balance'].fillna(0.0)
df['xrook_token_balance']=df['xrook_token_balance'].fillna(0.0)
df['total_balance']=df['total_balance'].fillna(0.0)
df=df.reset_index(drop=True)
df.info()
df.head()



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 752137 entries, 0 to 752136
Data columns (total 6 columns):
 #   Column               Non-Null Count   Dtype              
---  ------               --------------   -----              
 0   day                  752137 non-null  datetime64[ns, UTC]
 1   address              752137 non-null  object             
 2   status               752137 non-null  object             
 3   rook_token_balance   752137 non-null  float64            
 4   xrook_token_balance  752137 non-null  float64            
 5   total_balance        752137 non-null  float64            
dtypes: datetime64[ns, UTC](1), float64(3), object(2)
memory usage: 34.4+ MB


day                                     address  \
0 2020-12-31 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
1 2020-12-31 00:00:00+00:00  \xf286bb612e219916f8e9ba7200bf09ed218890cb   
2 2020-12-31 00:00:00+00:00  \xf55a73a366f1f9f03cef4cc10d3cd21e5c6a9026   
3 2020-12-31 00:00:00+00:00  \xcadf6735144d1d7f1a875a5561555cba5df2f75c   
4 2020-12-31 00:00:00+00:00  \xf30026fe8a2c0d01b70b1949ceaf2e09efd8b4a5   

     status  rook_token_balance  xrook_token_balance  total_balance  
0  excluded       653716.751872                  0.0  653716.751872  
1  included       100000.000000                  0.0  100000.000000  
2  included        51635.820509                  0.0   51635.820509  
3  included        28965.882114                  0.0   28965.882114  
4  included        18000.000000                  0.0   18000.000000

Open csv containing 'Excluded' addresses.

In [6]:
df_excluded_addresses = pd.read_csv('/content/gdrive/MyDrive/Colab Notebooks/22-0725_excluded_addresses.csv')
df_excluded_addresses.info()
df_excluded_addresses

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26 entries, 0 to 25
Data columns (total 4 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   label             26 non-null     object
 1   contract_address  26 non-null     object
 2   category          26 non-null     object
 3   status            26 non-null     object
dtypes: object(4)
memory usage: 960.0+ bytes


label                            contract_address  \
0         Rook Strategic Reserves  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
1                   Rook Treasury  \x9a67f1940164d0318612b497e8e6038f902a00a4   
2                      Sablier V1  \xcd18eaa163733da39c232722cbc4e8940b1d8888   
3                 Liquidity Pools  \x9bc9bdfe0843f44cf0878700501bb9142cdad2b8   
4                   Labs Multisig  \xa8b0a855be21568b93f32805b244158cc61ad006   
5         Rook: Liquidity Pool v4  \x4f868c1aa37fcf307ab38d215382e88fca6275e2   
6       Rook: Coordinator Staking  \x46168a99d15e6c620577d75ed7c453a6f53bafd5   
7   Rook: Hiding Game Distributor  \xd81e97075dbda444ef65db3a96706c679b5311fd   
8          Rook: HG 4 Distributor  \x25d27d026ab896fad8c8080f5b0e3fbd6667b139   
9          Rook: LPQ2 Distributor  \x2777b798fdfb906d42b89cf8f9de541db05dd6a1   
10         Rook: LPQ3 Distributor  \x59ff8975c813c1e70bdf2bcb8c02886928e4ea2d   
11         Rook: LPQ4 Distributor  \x9bc9bdfe0843f44cf0878700501bb9142cdad2b8   
12         Rook: LPQ5 Distributor  \x04caeb36be64222d5a9851503632b9e9d4a12501   
13                   Hiding Vault  \xfa5047c9c78b8877af97bdcb85db743fd7313d4a   
14                    Hiding Game  \xc00ba24ebcb6fb4aecbe5b78431ea49d608f5565   
15        Uniswap Pool: WETH-ROOK  \x70ec2fa6eccf4010eaf572d1c1a7bcbc72dec983   
16          Bancor Pool: BNT-ROOK  \xfa7b9ad60304119f59b172ef78b98d50cb9a5c98   
17      SushiSwap Pool: WETH-ROOK  \xf13eef1c6485348b9c9fa0d5df2d89accc5b0147   
18                   FTX Exchange  \x2faf487a4414fe77e2327f0bf4ae2a264a776ad2   
19                    FTX Deposit  \x15a8fb64b1c7296c66839b482d4c4dde3fa78b6c   
20                       Poloniex  \xa910f92acdaf488fa6ef02174fb86208ad7722ba   
21                         gateio  \x1c4b70a3968436b9a0a9cf5205c787eb81bb558c   
22                         gateio  \x0f4ee9631f4be0a63756515141281a3e2b293bbe   
23                         gateio  \x0d0707963952f2fba59dd06f2b425ace40b492fe   
24                         bitrue  \x6cc8dcbca746a6e4fdefb98e1d0df903b107fd21   
25                        Bittrex  \xfbb1b73c4f0bda4f67dca266ce6ef42f520fbb98   

          category    status  
0             Rook  excluded  
1             Rook  excluded  
2          Sablier  excluded  
3             Rook  excluded  
4             Rook  excluded  
5             Rook  excluded  
6             Rook  excluded  
7             Rook  excluded  
8             Rook  excluded  
9             Rook  excluded  
10            Rook  excluded  
11            Rook  excluded  
12            Rook  excluded  
13            Rook  excluded  
14            Rook  excluded  
15  Liquidity Pool  excluded  
16  Liquidity Pool  excluded  
17  Liquidity Pool  excluded  
18             CEX  excluded  
19             CEX  excluded  
20             CEX  excluded  
21             CEX  excluded  
22             CEX  excluded  
23             CEX  excluded  
24             CEX  excluded  
25             CEX  excluded

In [3]:
def change_status(_df, _addr, updated_status):
  _df.loc[_df['address'] == _addr, 'status'] = updated_status



# df.head()

In [10]:
change_status(df, '\x70ec2fa6eccf4010eaf572d1c1a7bcbc72dec983', 'included') #Uniswap pool - change to included
change_status(df, '\xfa7b9ad60304119f59b172ef78b98d50cb9a5c98', 'included') #Bancor pool - change to included
change_status(df, '\xf13eef1c6485348b9c9fa0d5df2d89accc5b0147', 'included') #Sushi pool - change to included

In [60]:
# df_500 = df[(df['total_balance'] > 500) & (df['status']=='included')].copy()
df_500 = df[(df['total_balance'] > 500)].copy()

In [61]:
# df_500 = df_500.reset_index(drop=True)
df_500['rook_token_balance']=df_500['rook_token_balance'].fillna(0.0)
df_500['xrook_token_balance']=df_500['xrook_token_balance'].fillna(0.0)
df_500['total_balance']=df_500['total_balance'].fillna(0.0)
df_500

day                                     address  \
0      2020-12-31 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
1      2020-12-31 00:00:00+00:00  \xf286bb612e219916f8e9ba7200bf09ed218890cb   
2      2020-12-31 00:00:00+00:00  \xf55a73a366f1f9f03cef4cc10d3cd21e5c6a9026   
3      2020-12-31 00:00:00+00:00  \xcadf6735144d1d7f1a875a5561555cba5df2f75c   
4      2020-12-31 00:00:00+00:00  \xf30026fe8a2c0d01b70b1949ceaf2e09efd8b4a5   
...                          ...                                         ...   
750321 2022-01-01 00:00:00+00:00  \x195fca8382363a06eeb3ab93aaa71b3aa3a337ca   
750322 2022-01-01 00:00:00+00:00  \xb8001c3ec9aa1985f6c747e25c28324e4a361ec1   
750323 2022-01-01 00:00:00+00:00  \x8d9f950c23b73edf79ce52f74c6fb589cd2cbd90   
750324 2022-01-01 00:00:00+00:00  \x80825bf6c668168c81cdde78bcea8d56dae92ed1   
750325 2022-01-01 00:00:00+00:00  \xd2d759c7f8d7101d6c2634048b9269136f97b149   

          status  rook_token_balance  xrook_token_balance  total_balance  
0       excluded       653716.751872                  0.0  653716.751872  
1       included       100000.000000                  0.0  100000.000000  
2       included        51635.820509                  0.0   51635.820509  
3       included        28965.882114                  0.0   28965.882114  
4       included        18000.000000                  0.0   18000.000000  
...          ...                 ...                  ...            ...  
750321  included          535.548066                  0.0     535.548066  
750322  included          517.703226                  0.0     517.703226  
750323  included          513.091384                  0.0     513.091384  
750324  included          512.521838                  0.0     512.521838  
750325  included          501.994575                  0.0     501.994575  

[35409 rows x 6 columns]

In [62]:
df_500_week = df_500.set_index('day').groupby([pd.Grouper(freq='W'), 'address', 'status']).mean()
df_500_week=df_500_week.reset_index()
df_500_week.head()

day                                     address  \
0 2020-11-01 00:00:00+00:00  \xaef38e99b9db5e96cab3ce5cbc29a3a1dfeffe71   
1 2020-11-01 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
2 2020-11-01 00:00:00+00:00  \xcadf6735144d1d7f1a875a5561555cba5df2f75c   
3 2020-11-01 00:00:00+00:00  \xf55a73a366f1f9f03cef4cc10d3cd21e5c6a9026   
4 2020-11-08 00:00:00+00:00  \x211b6a1137bf539b2750e02b9e525cf5757a35ae   

     status  rook_token_balance  xrook_token_balance  total_balance  
0  included         20000.00000                  0.0    20000.00000  
1  excluded        780000.00000                  0.0   780000.00000  
2  included         60000.00000                  0.0    60000.00000  
3  included        140000.00000                  0.0   140000.00000  
4  included          1341.98034                  0.0     1341.98034

In [63]:
df2['total_daily_balance']=df_500_week.groupby(['day'])['total_balance'].sum()
df2.head()


total_balance  total_balance  total_daily_balance
day                                                                         
2020-11-01 00:00:00+00:00  220000.000000            0.0       1000000.000000
2020-11-08 00:00:00+00:00  217669.077996            0.0        998339.699641
2020-11-15 00:00:00+00:00  215273.272792            0.0        995493.429844
2020-11-22 00:00:00+00:00  208045.759764            0.0        986276.951149
2020-11-29 00:00:00+00:00  200044.104910            0.0        979906.346334

In [64]:
df_500_week = pd.merge(df_500_week, df2['total_daily_balance'], how = 'left', on = 'day')
df_500_week.head() 

day                                     address  \
0 2020-11-01 00:00:00+00:00  \xaef38e99b9db5e96cab3ce5cbc29a3a1dfeffe71   
1 2020-11-01 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
2 2020-11-01 00:00:00+00:00  \xcadf6735144d1d7f1a875a5561555cba5df2f75c   
3 2020-11-01 00:00:00+00:00  \xf55a73a366f1f9f03cef4cc10d3cd21e5c6a9026   
4 2020-11-08 00:00:00+00:00  \x211b6a1137bf539b2750e02b9e525cf5757a35ae   

     status  rook_token_balance  xrook_token_balance  total_balance  \
0  included         20000.00000                  0.0    20000.00000   
1  excluded        780000.00000                  0.0   780000.00000   
2  included         60000.00000                  0.0    60000.00000   
3  included        140000.00000                  0.0   140000.00000   
4  included          1341.98034                  0.0     1341.98034   

   total_daily_balance  
0       1000000.000000  
1       1000000.000000  
2       1000000.000000  
3       1000000.000000  
4        998339.699641

In [205]:
df_500_week = df_500_week.assign(perc_of_daily_total = lambda x: (x.total_balance / x.total_daily_balance))
df_500_week.head()

day                                     address  \
0 2020-11-01 00:00:00+00:00  \xaef38e99b9db5e96cab3ce5cbc29a3a1dfeffe71   
1 2020-11-01 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
2 2020-11-01 00:00:00+00:00  \xcadf6735144d1d7f1a875a5561555cba5df2f75c   
3 2020-11-01 00:00:00+00:00  \xf55a73a366f1f9f03cef4cc10d3cd21e5c6a9026   
4 2020-11-08 00:00:00+00:00  \x211b6a1137bf539b2750e02b9e525cf5757a35ae   

     status  rook_token_balance  xrook_token_balance  total_balance  \
0  included         20000.00000                  0.0    20000.00000   
1  excluded        780000.00000                  0.0   780000.00000   
2  included         60000.00000                  0.0    60000.00000   
3  included        140000.00000                  0.0   140000.00000   
4  included          1341.98034                  0.0     1341.98034   

   total_daily_balance  perc_of_daily_total  
0       1000000.000000             0.020000  
1       1000000.000000             0.780000  
2       1000000.000000             0.060000  
3       1000000.000000             0.140000  
4        998339.699641             0.001344

In [234]:
from datetime import datetime, timedelta
today = pd.to_datetime('today', utc=True)
# previous_week = pd.to_datetime(today - timedelta(days=6)).floor('D')
previous_week = ((today - pd.Timedelta(days = 0)))

# print(previous_week.floor('D'))
# print(df_500_week['day'])
current_df_500_week = df_500_week.loc[df_500_week['day'] > previous_week]
format_dict = {'day':'{:%Y-%M-%D}', 'rook_token_balance': '{:,.0f}', 'xrook_token_balance':'{:,.0f}', 'total_balance': '{:,.0f}', 'total_daily_balance':'{:,.0f}', 'perc_of_daily_total': '{:,.3%}'}
current_df_500_week.head(10).style.format(format_dict)

# current_df_500_week.head()

# input = current_df_500_week.iloc[1]

# string = f'For the week of: {input.day}\nTotal Voting Balance: {np.format_float_positional(input.total_daily_balance, precision=2)}\n'

# print(string)
# # print(f"For the week of: {current_df_500_week['day'].iloc[1]}\nTotal Voting Balance: {(current_df_500_week['total_daily_balance'].iloc[1])}\n")
# # print(current_df_500_week[['day', 'total_daily_balance']].iloc[1])

In [235]:
input = current_df_500_week.iloc[1]

string = f'For the week of: {input.day}\nTotal Voting Balance: {np.format_float_positional(input.total_daily_balance, precision=2)}\n'

print(string)

For the week of: 2022-07-31 00:00:00+00:00
Total Voting Balance: 1209566.41



In [65]:
df[df['status'] == 'excluded']

day                                     address  \
0      2020-12-31 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
5      2020-12-31 00:00:00+00:00  \x70ec2fa6eccf4010eaf572d1c1a7bcbc72dec983   
298    2020-12-31 00:00:00+00:00  \x0d0707963952f2fba59dd06f2b425ace40b492fe   
1072   2020-12-30 00:00:00+00:00  \xb81f5b9bd373b9d0df2e3191a01b8fa9b4d2832a   
1077   2020-12-30 00:00:00+00:00  \x70ec2fa6eccf4010eaf572d1c1a7bcbc72dec983   
...                          ...                                         ...   
750341 2022-01-01 00:00:00+00:00  \x0d0707963952f2fba59dd06f2b425ace40b492fe   
750449 2022-01-01 00:00:00+00:00  \x25d27d026ab896fad8c8080f5b0e3fbd6667b139   
750591 2022-01-01 00:00:00+00:00  \xd81e97075dbda444ef65db3a96706c679b5311fd   
750837 2022-01-01 00:00:00+00:00  \x1c4b70a3968436b9a0a9cf5205c787eb81bb558c   
750887 2022-01-01 00:00:00+00:00  \x6cc8dcbca746a6e4fdefb98e1d0df903b107fd21   

          status  rook_token_balance  xrook_token_balance  total_balance  
0       excluded       653716.751872                  0.0  653716.751872  
5       excluded        11646.802346                  0.0   11646.802346  
298     excluded           80.041862                  0.0      80.041862  
1072    excluded       653716.751872                  0.0  653716.751872  
1077    excluded        11334.776515                  0.0   11334.776515  
...          ...                 ...                  ...            ...  
750341  excluded          434.084133                  0.0     434.084133  
750449  excluded          172.069595                  0.0     172.069595  
750591  excluded           83.194242                  0.0      83.194242  
750837  excluded           41.196077                  0.0      41.196077  
750887  excluded           37.766964                  0.0      37.766964  

[6280 rows x 6 columns]

In [16]:
# df_500[(df.day < '2021-01-01')].head(50)

In [82]:
alt.data_transformers.enable('data_server')
alt.renderers.enable('default')

alt.Chart(df_500_week).mark_area().encode(
    alt.X('day:T'),
    alt.Y('total_balance:Q'),
    alt.Color('address:N'),
    tooltip = [
               alt.Tooltip("address:N"),
               alt.Tooltip("day:T"),
               alt.Tooltip("rook_token_balance:Q", format=(",.0f")),
               alt.Tooltip("xrook_token_balance:Q", format=(",.0f")),
              #  alt.Tooltip("wallet_label:N"),
               alt.Tooltip("total_balance:Q", format=(",.0f")),
               alt.Tooltip("total_daily_balance:Q", format = (",.0f")),
               alt.Tooltip("perc_of_daily_total:Q", format = (".1%"))
    ]
).properties(height=800, width=1400)


alt.Chart(...)

In [99]:
alt.data_transformers.enable('data_server')
alt.renderers.enable('default')

alt.Chart(df_500_week).mark_area().encode(
    alt.X('day:T'),
    alt.Y('total_balance:Q'),
    alt.Color("address:N"),
    alt.Row("status:N"),
    # alt.Color("")
    tooltip = [
               alt.Tooltip("address:N"),
               alt.Tooltip("day:T"),
               alt.Tooltip("rook_token_balance:Q", format=(",.0f")),
               alt.Tooltip("xrook_token_balance:Q", format=(",.0f")),
              #  alt.Tooltip("wallet_label:N"),
               alt.Tooltip("total_balance:Q", format=(",.0f")),
               alt.Tooltip("total_daily_balance:Q", format = (",.0f")),
               alt.Tooltip("perc_of_daily_total:Q", format = (".1%"))
    ]
).properties(height=400, width=1600)

alt.Chart(...)

In [69]:
alt.data_transformers.enable('data_server')
alt.renderers.enable('default')

alt.Chart(df_500_week).mark_area().encode(
    alt.X('day:T'),
    alt.Y('total_balance:Q'),
    alt.Color('address:N'),
    tooltip = [
               alt.Tooltip("address:N"),
               alt.Tooltip("day:T"),
               alt.Tooltip("rook_token_balance:Q", format=(",.0f")),
               alt.Tooltip("xrook_token_balance:Q", format=(",.0f")),
              #  alt.Tooltip("wallet_label:N"),
               alt.Tooltip("total_balance:Q", format=(",.0f")),
               alt.Tooltip("total_daily_balance:Q", format = (",.0f")),
               alt.Tooltip("status:N")
    ]
).properties(height=800, width=1400)

alt.Chart(...)